<a href="https://colab.research.google.com/github/rodrigo0345/Aprof2/blob/main/Task2_YOLO_RESNET50_LSTM.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import torch
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import time

from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import normalize
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix, classification_report

import torch
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from torch.utils.data import random_split
from torch import Tensor
import torch.nn as nn
from torch.nn import CrossEntropyLoss
from torch.optim import SGD, Adam
from torch.nn.init import kaiming_uniform_
from torch.nn.init import xavier_uniform_
import torchvision.transforms as transforms
from torchvision.transforms import Compose
from torchvision.transforms import ToTensor
from torchvision.transforms import Normalize
from torchvision.transforms import Compose, Lambda, Normalize
from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score, accuracy_score, mean_absolute_error
import torch
import torch.nn.functional as F
import torchvision
from torchvision.transforms import Normalize
import torch.optim as optim
import seaborn as sns

# openpyxl é preciso ser instalado para TPUs NOTA APAGEUI O DECORD
!pip install openpyxl ultralytics
import os
import kornia

import av
# from torchinfo import summary
# from livelossplot import PlotLosses
from ultralytics import YOLO

import random

Defaulting to user installation because normal site-packages is not writeable



[notice] A new release of pip is available: 25.1.1 -> 25.2
[notice] To update, run: pip install --upgrade pip


# SEEDS

In [2]:
np.random.seed(0)
torch.manual_seed(0)
random.seed(0)

In [3]:
from ultralytics import YOLO
import torch

print(f"PyTorch version: {torch.__version__}")
print(f"CUDA available: {torch.cuda.is_available()}")
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

try:
    print("Attempting to load YOLO model...")
    model = YOLO('yolov8n.pt') # Ou o modelo que você usa
    model.to(device)
    model.eval() # Coloque em modo de avaliação
    print("YOLO model loaded and set to eval mode successfully.")

    dummy_input = torch.rand(1, 3, 224, 224).to(device) # Ajuste o tamanho se necessário
    print(f"Dummy input created with shape: {dummy_input.shape} on device: {dummy_input.device}")

    print("Attempting YOLO prediction...")
    with torch.no_grad():
        results = model(dummy_input, verbose=False)
    print("YOLO prediction successful.")

    if results and len(results) > 0 and hasattr(results[0], 'boxes') and results[0].boxes is not None:
        print(f"Number of boxes detected in the first result: {len(results[0].boxes)}")
    else:
        print("No boxes detected or results format is unexpected.")

except Exception as e:
    print(f"AN ERROR OCCURRED DURING ISOLATED YOLO TEST: {e}")
    import traceback
    traceback.print_exc()

PyTorch version: 2.7.0+cu128
CUDA available: True
Using device: cuda
Attempting to load YOLO model...


YOLO model loaded and set to eval mode successfully.
Dummy input created with shape: torch.Size([1, 3, 224, 224]) on device: cuda:0
Attempting YOLO prediction...


YOLO prediction successful.
Number of boxes detected in the first result: 0


In [4]:
path = "/mounts/OSS_dataset/Train_Task1_2/"
labels_path ="/mounts/OSS_dataset/Dataset_2024/Train/OSATS.xlsx"

info_df = pd.read_excel(labels_path)

video_files = [os.path.splitext(f)[0] for f in os.listdir(path) if os.path.isfile(os.path.join(path, f)) and f.endswith(('.mp4', '.avi', '.mov'))]
video_column = 'VIDEO'

info_df = info_df[info_df[video_column].isin(video_files)]
print(f"Number of videos: {len(info_df)}")
info_df.head()

Number of videos: 942


STUDENT       GROUP  TIME  SUTURES INVESTIGATOR VIDEO  OSATS_RESPECT  \
0  AHO729  E-LEARNING   PRE      1.0            A  P54M              2   
1  AHO729  E-LEARNING   PRE      1.0            B  P54M              2   
2  AHO729  E-LEARNING   PRE      1.0            C  P54M              2   
3  AHO729  E-LEARNING  POST      4.5            A  M45P              4   
4  AHO729  E-LEARNING  POST      4.5            B  M45P              2   

   OSATS_MOTION  OSATS_INSTRUMENT  OSATS_SUTURE  OSATS_FLOW  OSATS_KNOWLEDGE  \
0             1                 2             2           1                2   
1             1                 3             1           2                1   
2             1                 1             1           1                1   
3             4                 4             3           3                4   
4             3                 4             3           3                4   

   OSATS_PERFORMANCE  OSATS_FINAL_QUALITY  GLOBA_RATING_SCORE  
0                  2                    1                  13  
1                  2                    1                  13  
2                  1                    1                   9  
3                  3                    3                  28  
4                  3                    3                  25

In [5]:
OSATS_COLUMNS_INDIVIDUAL = [
    'OSATS_RESPECT', 'OSATS_MOTION', 'OSATS_INSTRUMENT',
    'OSATS_SUTURE', 'OSATS_FLOW', 'OSATS_KNOWLEDGE',
    'OSATS_PERFORMANCE', 'OSATS_FINAL_QUALITY'
]

def get_vector_of_ratings(video: str, source_df: pd.DataFrame):
    video_data = info_df[source_df['VIDEO'] == video]
    return video_data[OSATS_COLUMNS_INDIVIDUAL].iloc[0].values.tolist()

print(get_vector_of_ratings("A31H",info_df))


def update_info_df_with_binned_grs(df: pd.DataFrame):
    updated_df = df.copy()

    binned_scores_series = updated_df['VIDEO'].apply(
        lambda video_id: get_vector_of_ratings(video_id, updated_df)
    )

    scores_df_temp = pd.DataFrame(
        binned_scores_series.tolist(),
        columns=OSATS_COLUMNS_INDIVIDUAL,
        index=updated_df.index
    )

    for col_name in OSATS_COLUMNS_INDIVIDUAL:
        updated_df[col_name] = scores_df_temp[col_name]

    osats_score_vector_list = []
    videos_with_issues_for_vector = 0
    for index, row in updated_df.iterrows():
        current_vector = []
        valid_vector = True
        for col_name in OSATS_COLUMNS_INDIVIDUAL:
            score = row[col_name]
            if pd.isna(score):
                valid_vector = False
                break
            try:
                current_vector.append(float(score))
            except (ValueError, TypeError):
                valid_vector = False
                break

        if valid_vector and len(current_vector) == len(OSATS_COLUMNS_INDIVIDUAL):
            osats_score_vector_list.append(current_vector)
        else:
            osats_score_vector_list.append(None)
            videos_with_issues_for_vector += 1

    updated_df['OSATS_SCORE_VECTOR'] = osats_score_vector_list

    if updated_df['OSATS_SCORE_VECTOR'].isnull().any():
         num_null_vectors = updated_df['OSATS_SCORE_VECTOR'].isnull().sum()

    return updated_df

info_df = update_info_df_with_binned_grs(info_df)

[1, 2, 1, 1, 1, 2, 2, 1]


In [6]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

def to_device(data, device):
    if isinstance(data, (list, tuple)):
        return [to_device(x, device) for x in data]
    return data.to(device, non_blocking=True)

class DeviceDataLoader():
    def __init__(self, dl, device):
        self.dl = dl
        self.device = device

    def __iter__(self):
        for b in self.dl:
            yield to_device(b, self.device)

    def __len__(self):
        return len(self.dl)

print(device)

if device.type == 'cpu':
    print("No GPU found, skipping memory reservation.")
else:
    gpu_index = device.index
    os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "max_split_size_mb:512,garbage_collection_threshold:0.8" 

cuda


# Config

In [7]:
size = (256, 256)  # (height, width)


cfg = {
    "sampling_strategy": "fixed_step_sampling",
    "frame_division_factor": 75, # Ajuste este valor!
                                 # 30 (1 frame/segundo), 75 (aprox. 1 frame/2.5 segundos), 150, etc.
                                 # Quanto maior, menos frames iniciais são extraídos.
    "model_input_frames": 128,
    # Número fixo de frames que o modelo espera.
                                 # Experimente 64, 128, 256.
    "target_frame_height": size[0],
    "target_frame_width": size[1],


    # --- NEW PARAMETER ---
    # Power for non-linear frame sampling.
    # 1.0 = linear (even spacing, same as before)
    # 2.0 = quadratic (more frames from the end)
    # 3.0 = cubic (even MORE frames from the very end)
    "frame_sampling_power": 2.5
}

segments = 16
batch_size = 2
yolo_name = "yolo_preTrained.pt"

# Melhor ate agora "yolov5l6.pt" 

In [8]:
train_transform = Compose([
    ToTensor()
])

test_transform = Compose([
    ToTensor()
])

In [9]:
class VideoDataset(Dataset):
    def __init__(self, df_dataset, cfg, dataset_path, transformer, mean, std) -> None:
        super().__init__()
        self.df_dataset = df_dataset.reset_index(drop=True)
        self.dataset_path = dataset_path
        self.cfg = cfg
        self.label = [
            'OSATS_RESPECT', 'OSATS_MOTION', 'OSATS_INSTRUMENT',
            'OSATS_SUTURE', 'OSATS_FLOW', 'OSATS_KNOWLEDGE',
            'OSATS_PERFORMANCE', 'OSATS_FINAL_QUALITY'
        ]
        self.mean = mean
        self.std = std
        self.transformer = transformer

    def __len__(self):
        return len(self.df_dataset)

    def set_task_one(self):
        self.label = "GLOBA_RATING_SCORE"

    def set_task_two(self):
        self.label = [
            'OSATS_RESPECT', 'OSATS_MOTION', 'OSATS_INSTRUMENT',
            'OSATS_SUTURE', 'OSATS_FLOW', 'OSATS_KNOWLEDGE',
            'OSATS_PERFORMANCE', 'OSATS_FINAL_QUALITY'
        ]
    

    def __getitem__(self, idx):
        # --- 1. Get video path and target frame count ---
        video_info = self.df_dataset.iloc[idx]
        video_name = video_info["VIDEO"] + ".mp4"
        video_path = os.path.join(self.dataset_path, video_name)
        
        # This is 'x', the exact number of frames you want to extract
        target_T = self.cfg["model_input_frames"]
    
        try:
            container = av.open(video_path)
            stream = container.streams.video[0]
            total_frames = stream.frames
        except Exception as e:
            # Handle cases where the video file is corrupted or cannot be opened
            print(f"Error opening or reading video: {video_path}. Reason: {e}")
            print("Returning an empty tensor for this item.")
            # Return a tensor with the correct shape but 0 frames, and a dummy label
            C, H, W = 4, self.cfg["target_frame_height"], self.cfg["target_frame_width"]
            empty_frames = torch.zeros((target_T, C, H, W))
            dummy_label = torch.zeros(len(self.label)) if isinstance(self.label, list) else torch.tensor(0.0)
            return empty_frames, dummy_label
    
        # --- 2. Generate exactly `target_T` frame indices ---
        
        # Handle edge case of an empty video
        if total_frames == 0:
            print(f"Warning: Video {video_name} has 0 frames. Returning an empty tensor.")
            container.close()
            C, H, W = 4, self.cfg["target_frame_height"], self.cfg["target_frame_width"]
            empty_frames = torch.zeros((target_T, C, H, W))
            dummy_label = torch.zeros(len(self.label)) if isinstance(self.label, list) else torch.tensor(0.0)
            return empty_frames, dummy_label
    
        # As requested, print a warning if the assumption of having enough frames is false.
        # np.linspace will handle this by repeating frames, which is a good default behavior.
        if total_frames < target_T:
            print(f"Warning: Video {video_name} has only {total_frames} frames, "
                  f"which is less than the required {target_T}. Frames will be repeated.")
            
        # Get the sampling power from the config. Default to 1.0 for linear spacing.
        sampling_power = self.cfg.get("frame_sampling_power", 1.0)
    
        # A. Generate a linear space from 0.0 to 1.0
        linear_space = np.linspace(0, 1, target_T)
        
        # B. Apply the power function to create non-linear spacing
        # This will "bend" the space, concentrating points towards the end
        nonlinear_space = 1 - (1 - linear_space) ** sampling_power
        
        # C. Scale the non-linear space to the video's frame count
        # and convert to integers.
        indices = np.round(nonlinear_space * (total_frames - 1)).astype(int)

        #print("Linear frames indices:", np.round(linear_space * (total_frames - 1)).astype(int))
        # print()
        #print(f"Non-linear ({sampling_power}) frames indices:", indices)
        #print()
    
        # --- 3. Efficiently extract the frames ---
        frames_list = []
        # Use a dictionary to store frames by their index. This is robust for repeated indices.
        extracted_frames_dict = {}
        indices_to_get = set(indices) # Use a set for fast O(1) lookups
    
        frame_idx_counter = 0
        for frame in container.decode(video=0):
            if frame_idx_counter in indices_to_get:
                pil_image = frame.to_image().convert('RGB')
                transformed_frame = self.transformer(pil_image)
                extracted_frames_dict[frame_idx_counter] = transformed_frame
                
                # Optional: for very long videos, this can speed things up
                indices_to_get.remove(frame_idx_counter)
                if not indices_to_get:
                    break # Stop decoding once we have all the unique frames we need
            
            frame_idx_counter += 1
        
        container.close()
        
        # Re-order the extracted frames according to the `indices` array.
        # This correctly handles repeated frames for short videos.
        for index_val in indices:
            # Check if a frame was successfully extracted, otherwise something went wrong
            if index_val in extracted_frames_dict:
                frames_list.append(extracted_frames_dict[index_val])
            else:
                # This should be rare, but it's a good safeguard
                print(f"Error: Frame index {index_val} was requested but not found in video {video_name}. "
                      f"This might indicate a video decoding issue. Appending a zero tensor.")
                C, H, W = 4, self.cfg["target_frame_height"], self.cfg["target_frame_width"]
                frames_list.append(torch.zeros((C, H, W)))
    
        # --- 4. Stack frames and get labels ---
        if not frames_list:
            # This case should be caught earlier, but as a final safeguard:
            print(f"Error: No frames were extracted for video {video_name}. Returning an empty tensor.")
            C, H, W = 4, self.cfg["target_frame_height"], self.cfg["target_frame_width"]
            frames = torch.zeros((target_T, C, H, W))
        else:
            frames = torch.stack(frames_list, dim=0)
    
        # The old padding/truncating section is NO LONGER NEEDED because `frames`
        # will now always have a shape of (target_T, C, H, W).
        
        # --- Label extraction remains the same ---
        if isinstance(self.label, str):
            label = video_info[self.label]
            label = torch.tensor(label, dtype=torch.long) # Use long for classification labels
        else:
            label = [video_info[col] for col in self.label]
            label = torch.tensor(label, dtype=torch.float32)
    
        return frames, label


class AddKorniaEdgeChannel:
    """
    A custom transform that uses Kornia on the GPU to calculate the Sobel
    edge map and append it as a fourth channel.
    """
    def __init__(self, device):
        """
        Initializes the transform.
        Args:
            device (torch.device): The device (e.g., 'cuda:0') to perform operations on.
        """
        self.device = device

    def __call__(self, img_tensor):
        """
        Args:
            img_tensor (Tensor): A CPU tensor of size (3, H, W).
        Returns:
            Tensor: A CPU tensor with the edge channel, size (4, H, W).
        """
        if img_tensor.shape[0] != 3:
            raise ValueError("Input tensor must have 3 channels (RGB).")


        # 2. Perform all subsequent operations on the GPU
        img_tensor_batch = img_tensor.unsqueeze(0)
        gray_tensor_batch = kornia.color.rgb_to_grayscale(img_tensor_batch)
        edge_batch = kornia.filters.sobel(gray_tensor_batch)
        
        edge_magnitude = edge_batch.squeeze(0)

        # Normalization also happens on the GPU
        min_val, max_val = edge_magnitude.min(), edge_magnitude.max()
        edge_normalized = (edge_magnitude - min_val) / (max_val - min_val + 1e-6)

        # Concatenate the original GPU tensor and the new edge tensor
        output_tensor = torch.cat([img_tensor, edge_normalized], dim=0)
        
        # 3. CRITICAL: Move the final result back to the CPU before returning
        # The DataLoader worker needs a CPU tensor to collate with other samples.
        return output_tensor.cpu()


# task = 1 | 2
import json

mean = torch.tensor([0.485, 0.456, 0.406, 0.5])  # RGB + Edge channel
std = torch.tensor([0.229, 0.224, 0.225, 0.5])  # RGB + Edge channel

# edge_transform_gpu = AddKorniaEdgeChannel(device=device)
transformer = Compose([
    ToTensor(),
    transforms.Resize(size, antialias=True),  
    # edge_transform_gpu,
    AddKorniaEdgeChannel(device=device),
    Normalize(mean=mean, std=std)
])

# task = 1 | 2
def prepare_data_loaders(path_train, json_path="/mounts/OSS_dataset/data_split.json", task=1): # 'segments' removido do parâmetro
    json_file = open(json_path)
    split_data = json.load(json_file)
    json_file.close()

    train_videos = split_data['train']
    val_videos = split_data['val']
    video_column = 'VIDEO'

    # Get rows where the City is either 'Chicago' or 'Los Angeles'
    train_df = info_df.loc[info_df[video_column].isin(train_videos)]
    val_df = info_df.loc[info_df[video_column].isin(val_videos)]
    
    train_df, test_df = train_test_split(train_df, test_size=0.2, random_state=42, shuffle=True)

    # Reusar o cfg global
    train_dataset = VideoDataset(train_df, cfg, path_train, transformer, mean, std)
    val_dataset = VideoDataset(val_df, cfg, path_train, transformer, mean, std)
    test_dataset = VideoDataset(test_df, cfg, path_train, transformer, mean, std)

    train_dataset.set_task_one() if task == 1 else train_dataset.set_task_two()
    val_dataset.set_task_one() if task == 1 else val_dataset.set_task_two()
    test_dataset.set_task_one() if task == 1 else test_dataset.set_task_two()

    train_labels = train_df['GLOBA_RATING_SCORE'].values

    # 2. Calcular os pesos para cada classe
    class_counts = np.bincount(train_labels)
    class_weights = 1. / class_counts
    sample_weights = np.array([class_weights[t] for t in train_labels])
    sample_weights = torch.from_numpy(sample_weights).double()

    # 3. Criar o sampler
    sampler = torch.utils.data.WeightedRandomSampler(weights=sample_weights, num_samples=len(sample_weights), replacement=True)

    train_loader = DataLoader(
        train_dataset,
        batch_size=batch_size,
        num_workers=4,
        pin_memory=True,
        sampler=sampler 
    )
    
    val_loader = DataLoader(
    val_dataset,
    batch_size=batch_size,
    shuffle=False, 
    num_workers=4,
    pin_memory=True
    )

    test_loader = DataLoader(
    test_dataset,
    batch_size=batch_size,
    shuffle=False,
    num_workers=4,
    pin_memory=True
    )
    return train_loader, val_loader, test_loader, train_dataset

# Chamada para preparar os dataloaders
train_dl, val_dl, test_dl, train_dataset = prepare_data_loaders(path, task = 2)

torch.cuda.synchronize()
print(torch.cuda.memory_allocated())
print(torch.cuda.memory_reserved())

46791168
96468992


/tmp/ipykernel_3928599/1113887339.py:234: RuntimeWarning: divide by zero encountered in divide
  class_weights = 1. / class_counts


In [10]:
import torch
import torch.nn as nn
import torch.optim as optim # Ensure optim is imported

# Assume device is defined globally or passed appropriately
# Assume NUM_SCORES_PER_CATEGORY = 5 is globally available or passed

def train_model(model, train_loader, val_loader, num_epochs=5, learning_rate=0.001, current_task_type="task2"):
    model = model.to(device)
    criterion = nn.CrossEntropyLoss()
    optimizer = optim.Adam(filter(lambda p: p.requires_grad, model.parameters()), lr=learning_rate)

    # This should be accessible if defined in the same scope or globally
    # For this example, let's explicitly state it for clarity in this function,
    # but ideally, it's passed or accessed from a config.
    # NUM_SCORES_PER_CATEGORY_CONST = 5 # As per your global definition

    for epoch in range(num_epochs):
        model.train()
        train_loss = 0.0
        train_correct_osats_scores = 0
        train_total_osats_scores = 0

        print(f"Starting Epoch: {epoch+1}/{num_epochs}")
        for videos, labels in train_loader:
            if videos.numel() == 0 or labels.numel() == 0 : continue
            videos = videos.to(device) # (B, C, T, H, W)
            original_labels = labels.to(device, dtype=torch.long) # For Task 2: (B, NUM_OSATS_CATEGORIES)

            # --- IMPORTANT MODIFICATION: Convert labels to 0-indexed ---
            # Assuming original labels are 1-indexed (e.g., 1 to NUM_SCORES_PER_CATEGORY)
            # We need them to be 0-indexed (e.g., 0 to NUM_SCORES_PER_CATEGORY - 1)
            # A quick check: if labels.min() < 0 or labels.max() >= NUM_SCORES_PER_CATEGORY (using 0-indexed logic for max)
            # For 1-indexed, they would be 1 to NUM_SCORES_PER_CATEGORY
            # So, if labels.min() < 1 or labels.max() > NUM_SCORES_PER_CATEGORY, there's an issue.
            # The error "Target 5 is out of bounds" for NUM_SCORES_PER_CATEGORY=5 confirms 1-indexing is likely.
            labels_0_indexed = original_labels - 1
            # ------------------------------------------------------------

            optimizer.zero_grad()
            outputs = model(videos) # For Task 2: (B, NUM_SCORES_PER_CATEGORY, NUM_OSATS_CATEGORIES)

            # Task 2 specific loss and accuracy, using 0-indexed labels
            loss = criterion(outputs, labels_0_indexed)
            _, predicted_scores = torch.max(outputs, 1) # Max over NUM_SCORES_PER_CATEGORY dim -> (B, NUM_OSATS_CATEGORIES)
                                                        # predicted_scores are already 0-indexed (0 to C-1)

            train_total_osats_scores += labels_0_indexed.numel() # Total individual OSATS scores in batch
            train_correct_osats_scores += (predicted_scores == labels_0_indexed).sum().item()

            loss.backward()
            optimizer.step()
            train_loss += loss.item() * videos.size(0)


        avg_train_loss = train_loss / len(train_loader.dataset) if len(train_loader.dataset) > 0 else 0
        train_accuracy = train_correct_osats_scores / train_total_osats_scores if train_total_osats_scores > 0 else 0

        model.eval()
        val_loss = 0.0
        val_correct_osats_scores = 0
        val_total_osats_scores = 0
        with torch.no_grad():
            for videos, labels in val_loader:
                if videos.numel() == 0 or labels.numel() == 0 : continue
                videos = videos.to(device)
                original_labels = labels.to(device, dtype=torch.long)

                # --- IMPORTANT MODIFICATION: Convert labels to 0-indexed ---
                labels_0_indexed = original_labels - 1
                # ------------------------------------------------------------

                outputs = model(videos)

                loss = criterion(outputs, labels_0_indexed)
                _, predicted_scores = torch.max(outputs, 1) # predicted_scores are 0-indexed
                val_total_osats_scores += labels_0_indexed.numel()
                val_correct_osats_scores += (predicted_scores == labels_0_indexed).sum().item()
                val_loss += loss.item() * videos.size(0)

        avg_val_loss = val_loss / len(val_loader.dataset) if len(val_loader.dataset) > 0 else 0
        val_accuracy = val_correct_osats_scores / val_total_osats_scores if val_total_osats_scores > 0 else 0

        print(f"Epoch {epoch+1}/{num_epochs}, Train Loss: {avg_train_loss:.4f}, Train Acc: {train_accuracy:.4f}, "
              f"Val Loss: {avg_val_loss:.4f}, Val Acc: {val_accuracy:.4f}")
    return model

In [ ]:
import torch
import torch.nn as nn
import torchvision.models as models
import torch.optim as optim
from torchvision.transforms import Compose, Resize, Normalize
import torchvision.transforms.functional as TF
import numpy as np # For linspace if needed, though torch.linspace is better

# Conditional YOLO import (copied from prompt)
try:
    from ultralytics import YOLO
except ImportError:
    print("Warning: ultralytics.YOLO not found. Using a MockYOLO class. Training will not be functional with real YOLO.")
    class MockYOLOResults:
        def __init__(self):
            self.boxes = None
    class MockYOLO(nn.Module):
        def __init__(self, model_name='yolov8n.pt'):
            super().__init__()
            self.model_name = model_name
            self.dummy_param = nn.Parameter(torch.empty(0))
        def forward(self, imgs, verbose=False):
            if isinstance(imgs, torch.Tensor): batch_size = imgs.shape[0]
            elif isinstance(imgs, list): batch_size = len(imgs)
            else: batch_size = 1
            return [MockYOLOResults() for _ in range(batch_size)]
    YOLO = MockYOLO

# --- Constants and helper functions ---
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
NUM_OSATS_CATEGORIES = 8
NUM_SCORES_PER_CATEGORY = 5
RESNET_INPUT_SIZE = (224, 224)

VIDEODATASET_MEAN_TENSOR = torch.tensor([0.5, 0.5, 0.5], device=device)
VIDEODATASET_STD_TENSOR = torch.tensor([0.5, 0.5, 0.5], device=device)

resnet_roi_transform = Compose([
    Resize(RESNET_INPUT_SIZE, antialias=True),
    Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

def denormalize_frame_for_detector(normalized_frame_chw_tensor_on_device):
    mean = VIDEODATASET_MEAN_TENSOR
    std = VIDEODATASET_STD_TENSOR
    if mean.ndim == 1:
        mean = mean.view(-1, 1, 1)
        std = std.view(-1, 1, 1)
    frame_0_1 = normalized_frame_chw_tensor_on_device * std.to(normalized_frame_chw_tensor_on_device.device) + \
                mean.to(normalized_frame_chw_tensor_on_device.device)
    return frame_0_1.clamp_(0, 1)



def get_best_roi_from_yolo_pred_and_crop(
    yolo_pred_tensor,
    original_frame_chw_on_device: torch.Tensor,
    score_threshold: float = 0.75,
    target_class_idx: int = None,
    min_roi_size: int = 10  # Adicionamos um tamanho mínimo para o ROI
) -> torch.Tensor:
    best_box_coords = None
    max_score = score_threshold

    for det in yolo_pred_tensor:
        current_score = det[4].item()
        current_class_idx = int(det[5].item())

        if target_class_idx is not None and current_class_idx != target_class_idx:
            continue
        
        if current_score > max_score:
            max_score = current_score
            best_box_coords = (det[0].item(), det[1].item(), det[2].item(), det[3].item())

    C, H, W = original_frame_chw_on_device.shape
    
    # 1. TENTAR USAR O ROI DETETADO
    if best_box_coords is not None:
        xmin, ymin, xmax, ymax = best_box_coords
        xmin = max(0, min(xmin, W - 1))
        ymin = max(0, min(ymin, H - 1))
        xmax = max(xmin + 1, min(xmax, W))
        ymax = max(ymin + 1, min(ymax, H))

        top, left = int(round(ymin)), int(round(xmin))
        height, width = int(round(ymax - ymin)), int(round(xmax - xmin))

        # 2. VERIFICAÇÃO DE ROBUSTEZ: O ROI é grande o suficiente?
        if height >= min_roi_size and width >= min_roi_size:
            # Se for, recortamos e retornamos.
            return TF.crop(original_frame_chw_on_device, top, left, height, width)
        else:
            pass
            # Se for muito pequeno, imprimimos um aviso e usamos o fallback abaixo.
            # print(f"Warning: Detected RoI is too small ({height}x{width}). Using center crop fallback.")

    ph, pw = H // 2, W // 2
    pt, pl = (H - ph) // 2, (W - pw) // 2
    
    # Esta parte agora é alcançada se não houver deteções ou se a deteção for inválida
    return TF.crop(original_frame_chw_on_device, pt, pl, ph, pw)
class Score_Classifier_Heads_Task2(nn.Module):
    def __init__(self, num_osats_categories, num_scores_per_osats_cat, input_features_dim):
        super().__init__()
        self.osats_heads = nn.ModuleList([
            nn.Linear(input_features_dim, num_scores_per_osats_cat)
            for _ in range(num_osats_categories)
        ])
    def forward(self, features_batch):
        head_outputs = [head(features_batch) for head in self.osats_heads]
        stacked_outputs = torch.stack(head_outputs, dim=1)
        return stacked_outputs.permute(0, 2, 1)

class TwoStage_VideoScoringModel_YOLO_ResNet_LSTM_Task2(nn.Module):
    def __init__(self,
                 yolo_model_name='yolov8n.pt',
                 detector_score_thresh=0.25,
                 target_yolo_class_idx=None,
                 num_frames_for_lstm=5,
                 lstm_hidden_size=512,
                 lstm_num_layers=1,
                 lstm_dropout=0.0):
        super().__init__()
        self.detector_score_threshold = detector_score_thresh
        self.target_yolo_class_idx = target_yolo_class_idx
        self.num_frames_for_lstm = num_frames_for_lstm

        print(f"Initializing YOLO detector ({yolo_model_name}) on device: {device}")
        self.detector = torch.hub.load('ultralytics/yolov5', 'custom', path=yolo_model_name) 
        self.detector.to(device)
        self.detector.eval()
        print("Freezing YOLO detector parameters.")
        for param in self.detector.parameters():
            param.requires_grad = False

        print("Initializing ResNet50 backbone for RoI feature extraction...")
        self.roi_feature_extractor = models.resnet50(weights=models.ResNet50_Weights.DEFAULT)
        self.backbone_out_features = self.roi_feature_extractor.fc.in_features
        self.roi_feature_extractor.fc = nn.Identity()
        self.roi_feature_extractor.to(device)

        print(f"Initializing LSTM layer (hidden_size={lstm_hidden_size}, num_layers={lstm_num_layers}, dropout={lstm_dropout if lstm_num_layers > 1 else 0.0})...")
        self.lstm_hidden_size = lstm_hidden_size
        self.lstm_num_layers = lstm_num_layers
        self.lstm = nn.LSTM(
            input_size=self.backbone_out_features,
            hidden_size=self.lstm_hidden_size,
            num_layers=self.lstm_num_layers,
            batch_first=True,
            dropout=lstm_dropout if lstm_num_layers > 1 else 0.0
        )
        self.lstm.to(device)

        print("Initializing Score Classifier heads for Task 2...")
        self.score_classifier = Score_Classifier_Heads_Task2(
            NUM_OSATS_CATEGORIES,
            NUM_SCORES_PER_CATEGORY,
            self.lstm_hidden_size
        ).to(device)

        self.roi_transform = resnet_roi_transform

    def train(self, mode: bool = True):
        self.training = mode
        self.roi_feature_extractor.train(mode)
        self.lstm.train(mode)
        self.score_classifier.train(mode)
        if self.detector is not None:
            self.detector.eval()
        return self

    def forward(self, video_clips_batch):
        B, T, C, H_proc, W_proc = video_clips_batch.shape
        
        actual_num_frames_to_sample = min(T, self.num_frames_for_lstm)

        if actual_num_frames_to_sample <= 0 :
            print(f"Warning: Clip length T={T} is too short or invalid. Using dummy LSTM input.")
            dummy_lstm_input = torch.zeros(B, self.num_frames_for_lstm, self.backbone_out_features,
                                           device=device, dtype=video_clips_batch.dtype)
            lstm_out, (h_n, c_n) = self.lstm(dummy_lstm_input)
            features_for_classifier = h_n[-1]
            scores = self.score_classifier(features_for_classifier)
            return scores

        if actual_num_frames_to_sample == 1:
            frame_indices = torch.tensor([T // 2], device=device, dtype=torch.long)
        else:
            frame_indices = torch.linspace(0, T - 1, steps=actual_num_frames_to_sample, device=device).long()

        selected_frames_ds_norm = video_clips_batch[:, frame_indices, :, :, :]

        individual_frames_ds_norm = selected_frames_ds_norm.contiguous().view(
            B * actual_num_frames_to_sample, C, H_proc, W_proc
        )
        

        rgb_frames_for_yolo = individual_frames_ds_norm[:, :3, :, :]

        mean_b = VIDEODATASET_MEAN_TENSOR.view(1, -1, 1, 1).to(device)
        std_b = VIDEODATASET_STD_TENSOR.view(1, -1, 1, 1).to(device)
        individual_frames_0_1_batch = (rgb_frames_for_yolo * std_b) + mean_b
        individual_frames_0_1_batch = individual_frames_0_1_batch.clamp_(0, 1)

        with torch.no_grad():
            yolo_preds_tensor_list = self.detector(individual_frames_0_1_batch)

        processed_rois_for_all_frames = []

        for i in range(B * actual_num_frames_to_sample):
            yolo_pred_tensor_single = yolo_preds_tensor_list[i]
            frame_0_1_single = individual_frames_0_1_batch[i]

            roi_0_1_tensor = get_best_roi_from_yolo_pred_and_crop(
                yolo_pred_tensor_single,
                frame_0_1_single,
                self.detector_score_threshold,
                self.target_yolo_class_idx
            )

            processed_roi = self.roi_transform(roi_0_1_tensor)

            processed_rois_for_all_frames.append(processed_roi)

        final_rois_tensor_all_frames = torch.stack(processed_rois_for_all_frames)

        if not processed_rois_for_all_frames:
            print("CRITICAL FALLBACK: No RoIs processed from any frame. Using dummy LSTM input.")
            dummy_lstm_input = torch.zeros(B, self.num_frames_for_lstm, self.backbone_out_features,
                                           device=device, dtype=video_clips_batch.dtype)
            lstm_out, (h_n, c_n) = self.lstm(dummy_lstm_input)
            features_for_classifier = h_n[-1]
            scores = self.score_classifier(features_for_classifier)
            return scores

        final_rois_tensor_all_frames = torch.stack(processed_rois_for_all_frames)

        roi_features_all_frames = self.roi_feature_extractor(final_rois_tensor_all_frames)

        sequence_features = roi_features_all_frames.view(B, actual_num_frames_to_sample, self.backbone_out_features)

        if actual_num_frames_to_sample < self.num_frames_for_lstm:
            padding_size = self.num_frames_for_lstm - actual_num_frames_to_sample
            padding = torch.zeros(B, padding_size, self.backbone_out_features,
                                  device=device, dtype=sequence_features.dtype)
            lstm_input = torch.cat([sequence_features, padding], dim=1)
        else:
            lstm_input = sequence_features

        lstm_out, (h_n, c_n) = self.lstm(lstm_input)
        features_for_classifier = h_n[-1]

        scores = self.score_classifier(features_for_classifier)
        return scores

In [ ]:
import torch
import torch.nn as nn
import torchvision.models as models



if train_dl and val_dl and len(train_dl.dataset) > 0 and len(val_dl.dataset) > 0:
    num_lstm_sequence_frames = 128 # Queremos usar 8 quadros para a LSTM

    video_scoring_model_task2 = TwoStage_VideoScoringModel_YOLO_ResNet_LSTM_Task2(
    yolo_model_name= yolo_name,
    detector_score_thresh=0.75,     # Ou seu valor desejado
    target_yolo_class_idx=None,
    num_frames_for_lstm=num_lstm_sequence_frames, # Especifica o comprimento da sequência
    lstm_hidden_size=2024,
    lstm_num_layers=3,
    lstm_dropout=0.6
).to(device)

    total_params = sum(p.numel() for p in video_scoring_model_task2.parameters())
    trainable_params = sum(p.numel() for p in video_scoring_model_task2.parameters() if p.requires_grad)
    print(f"Total model parameters: {total_params:,}")
    print(f"Trainable model parameters: {trainable_params:,}")

    trained_model_task2 = train_model(
        video_scoring_model_task2,
        train_dl,
        val_dl,
        num_epochs=15,
        learning_rate=1e-4
    )

    torch.save(trained_model_task2.state_dict(), "YOLO_RESNET50_LSTM_V1_state_dict.pth")
    print("Model state_dict saved to YOLO_RESNET50_V1_state_dict.pth")

else:
    print(f"Could not prepare dataloaders for or datasets are empty. Skipping model instantiation and training.")
    if train_dl: print(f"Train Dataloader dataset size: {len(train_dl.dataset)}")
    if val_dl: print(f"Validation Dataloader dataset size: {len(val_dl.dataset)}")

Initializing YOLO detector (yolo_preTrained.pt) on device: cuda


Using cache found in /mounts/tf2/.cache/torch/hub/ultralytics_yolov5_master


YOLOv5 🚀 2025-7-23 Python-3.10.16 torch-2.7.0+cu128 CUDA:0 (NVIDIA RTX A6000, 48548MiB)



Fusing layers... 


Model summary: 212 layers, 20881221 parameters, 0 gradients, 47.9 GFLOPs


...

/mounts/tf2/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:879: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


/mounts/tf2/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:879: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


/mounts/tf2/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:879: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


Epoch 15/15, Train Loss: 0.5081, Train Acc: 0.7829, Val Loss: 1.1840, Val Acc: 0.5585


Model state_dict saved to YOLO_RESNET50_V1_state_dict.pth


In [ ]:
import numpy as np
import torch
import torch.nn as nn
from sklearn.metrics import mean_absolute_error, f1_score, accuracy_score, classification_report, precision_recall_fscore_support
import traceback


def evaluate_model_task2(model, test_loader, device,
                         num_osats_categories,
                         num_scores_per_category,
                         osats_category_names=None):
    model = model.to(device)
    model.eval()
    criterion = nn.CrossEntropyLoss(reduction='mean')
    accumulated_loss_x_batch_size = 0.0
    total_samples_processed = 0
    all_predictions_list = []
    all_true_labels_list = []

    with torch.no_grad():
        for videos, original_labels_from_loader in test_loader:
            if videos.numel() == 0 or original_labels_from_loader.numel() == 0:
                print("Aviso: Batch vazio encontrado e pulado.")
                continue
            current_batch_size = videos.size(0)
            videos = videos.to(device)
            original_labels_1_indexed = original_labels_from_loader.to(device, dtype=torch.long)
            labels_0_indexed = original_labels_1_indexed - 1
            outputs = model(videos)
            loss = criterion(outputs, labels_0_indexed)
            accumulated_loss_x_batch_size += loss.item() * current_batch_size
            total_samples_processed += current_batch_size
            _, predicted_scores_0_indexed = torch.max(outputs, dim=1)
            all_predictions_list.append(predicted_scores_0_indexed.cpu().numpy())
            all_true_labels_list.append(labels_0_indexed.cpu().numpy())

    if not all_true_labels_list or total_samples_processed == 0:
        print("Nenhum dado processado no test_loader.")
        return 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, {}

    predictions_np = np.concatenate(all_predictions_list, axis=0)
    true_labels_np = np.concatenate(all_true_labels_list, axis=0)
    avg_test_loss = accumulated_loss_x_batch_size / total_samples_processed if total_samples_processed > 0 else 0.0
    test_mae_overall = mean_absolute_error(true_labels_np, predictions_np)

    per_category_f1_scores_macro = []
    per_category_f1_scores_weighted = []
    supports_for_weighted_f1 = []

    if num_osats_categories > 0:
        for i in range(num_osats_categories):
            true_cat_labels = true_labels_np[:, i]
            pred_cat_labels = predictions_np[:, i]
            f1_cat_macro = f1_score(true_cat_labels, pred_cat_labels, average='macro', zero_division=0)
            f1_cat_weighted = f1_score(true_cat_labels, pred_cat_labels, average='weighted', zero_division=0)
            per_category_f1_scores_macro.append(f1_cat_macro)
            per_category_f1_scores_weighted.append(f1_cat_weighted)
            supports_for_weighted_f1.append(len(true_cat_labels))

    test_f1_macro_overall = np.mean(per_category_f1_scores_macro) if per_category_f1_scores_macro else 0.0
    if per_category_f1_scores_weighted and sum(supports_for_weighted_f1) > 0:
        test_f1_weighted_overall = np.average(per_category_f1_scores_weighted, weights=supports_for_weighted_f1)
    else:
        test_f1_weighted_overall = 0.0

    # --- REVISED F1 SAMPLES ---
    sample_f1_scores = []
    if true_labels_np.shape[0] > 0 and num_osats_categories > 0: # Ensure there are samples and categories
        for i in range(true_labels_np.shape[0]): # Iterate over each sample
            true_sample_labels = true_labels_np[i, :] # (num_osats_categories,)
            pred_sample_labels = predictions_np[i, :] # (num_osats_categories,)

            tp_sample = np.sum(true_sample_labels == pred_sample_labels)

            precision_sample = tp_sample / num_osats_categories if num_osats_categories > 0 else 0.0
            recall_sample = tp_sample / num_osats_categories if num_osats_categories > 0 else 0.0

            if precision_sample + recall_sample == 0:
                f1_s = 0.0
            else:
                f1_s = 2 * (precision_sample * recall_sample) / (precision_sample + recall_sample)
            sample_f1_scores.append(f1_s)

        test_f1_samples = np.mean(sample_f1_scores) if sample_f1_scores else 0.0
    else:
        test_f1_samples = 0.0
    # --- END OF REVISED F1 SAMPLES ---

    per_category_accuracy_list = []
    avg_accuracy_across_categories = 0.0
    if num_osats_categories > 0:
        for i in range(num_osats_categories):
            acc = accuracy_score(true_labels_np[:, i], predictions_np[:, i])
            per_category_accuracy_list.append(acc)
        if per_category_accuracy_list:
            avg_accuracy_across_categories = np.mean(per_category_accuracy_list)

    exact_match_ratio = 0.0
    if true_labels_np.shape[0] > 0: # Check if there are any samples
        # Compare entire rows. np.all(axis=1) checks if all elements in a row are True.
        # (true_labels_np == predictions_np) gives a boolean array of same shape.
        # np.all(..., axis=1) reduces it to (num_samples,), True if all outputs matched for that sample.
        # np.sum(...) counts how many samples had all outputs matching.
        # Then divide by the total number of samples.
        num_exact_matches = np.sum(np.all(true_labels_np == predictions_np, axis=1))
        exact_match_ratio = num_exact_matches / true_labels_np.shape[0]

    print(f"\n--- Métricas de Avaliação no Conjunto de Teste (Task 2) ---")
    print(f"Loss Médio por Predição Individual (CrossEntropy): {avg_test_loss:.4f}")
    print(f"Mean Absolute Error (MAE Médio por Categoria, 0-indexed): {test_mae_overall:.4f}")
    print(f"F1 Score (Macro Overall - Média dos F1-macro por Categoria): {test_f1_macro_overall:.4f}")
    print(f"F1 Score (Weighted Overall - Média Ponderada dos F1-weighted por Categoria): {test_f1_weighted_overall:.4f}")
    print(f"F1 Score (Samples - Média das F1 por Amostra): {test_f1_samples:.4f}")
    print(f"Acurácia (Média por Categoria OSATS): {avg_accuracy_across_categories:.4f}")
    print(f"Acurácia (Exact Match Ratio / Correspondência Exata do Subconjunto): {exact_match_ratio:.4f}")

    print("\n--- Relatório de Classificação Detalhado por Categoria OSATS ---")
    # ... (rest of your classification report logic, which is fine) ...
    detailed_reports = {}
    if osats_category_names is None or len(osats_category_names) != num_osats_categories:
        if num_osats_categories > 0:
            print(f"Aviso: Nomes das categorias OSATS não fornecidos ou com tamanho incorreto. Usando nomes genéricos.")
        osats_category_names_internal = [f"Categoria_{i+1}" for i in range(num_osats_categories)]
    else:
        osats_category_names_internal = osats_category_names

    report_class_indices = list(range(num_scores_per_category))
    target_names_for_scores = [f"Class {j}" for j in report_class_indices]

    if num_osats_categories > 0:
        for i in range(num_osats_categories):
            cat_name = osats_category_names_internal[i]
            print(f"\n-- {cat_name} --")
            true_cat_labels = true_labels_np[:, i]
            pred_cat_labels = predictions_np[:, i]
            try:
                report_str = classification_report(
                    true_cat_labels,
                    pred_cat_labels,
                    labels=report_class_indices,
                    target_names=target_names_for_scores,
                    zero_division=0,
                    digits=3
                )
                print(report_str)
                detailed_reports[cat_name] = report_str
            except ValueError as e:
                print(f"Não foi possível gerar o relatório de classificação para {cat_name}: {e}")
                if true_cat_labels is not None: print(f"Labels verdadeiros únicos para {cat_name}: {np.unique(true_cat_labels)}")
                if pred_cat_labels is not None: print(f"Labels previstos únicos para {cat_name}: {np.unique(pred_cat_labels)}")
                detailed_reports[cat_name] = f"Erro ao gerar relatório: {e}"
            except IndexError as e:
                print(f"Erro de índice ao acessar categoria {i} para {cat_name}: {e}")
                detailed_reports[cat_name] = f"Erro de índice: {e}"
    elif total_samples_processed > 0:
        print("Nenhuma categoria OSATS definida (num_osats_categories = 0), relatório detalhado por categoria não aplicável.")


    return (avg_test_loss, test_mae_overall, test_f1_macro_overall, test_f1_weighted_overall,
            test_f1_samples, avg_accuracy_across_categories, exact_match_ratio, detailed_reports)

model_path = "YOLO_RESNET50_LSTM_V1_state_dict.pth"

num_lstm_sequence_frames = 128

model_task2_eval = TwoStage_VideoScoringModel_YOLO_ResNet_LSTM_Task2(
    yolo_model_name= yolo_name,
    detector_score_thresh=0.75,     # Yolo minium thresh hold
    target_yolo_class_idx=None,
    num_frames_for_lstm=num_lstm_sequence_frames, # Especifica o comprimento da sequência
    lstm_hidden_size=2024,
    lstm_num_layers=3,
    lstm_dropout=0.6
).to(device)


print(f"Verificando model_task2_eval: {type(model_task2_eval)}")


try:
    # 2. Carregue o dicionário de pesos do arquivo
    print(f"Tentando carregar o arquivo de pesos de: {model_path}")
    loaded_state_dict = torch.load(model_path, map_location=device)
    print("Arquivo de pesos carregado na memória com sucesso.")

    # 3. Use o MÉTODO .load_state_dict() DO SEU OBJETO model_task2_eval
    #    Passe strict=False para ignorar as chaves não correspondentes do detector YOLO.
    print("Tentando carregar os pesos no modelo (strict=False)...")
    missing_keys, unexpected_keys = model_task2_eval.load_state_dict(loaded_state_dict, strict=False)

    print(f"Pesos carregados no modelo a partir de {model_path}")

    # Opcional: Imprimir informações sobre chaves não correspondentes para verificação
    # if missing_keys:
    #     print("\nAviso: As seguintes chaves estavam faltando no state_dict carregado e não foram carregadas (o modelo usou seus pesos iniciais para estas):")
    #     for key in missing_keys:
    #         print(f"  - {key}")
    # if unexpected_keys:
    #     print("\nAviso: As seguintes chaves estavam no state_dict carregado mas não na arquitetura do modelo e foram ignoradas:")
    #     for key in unexpected_keys:
    #         print(f"  - {key}")

    # if not missing_keys and not unexpected_keys:
    #     print("Todas as chaves corresponderam perfeitamente.")
    # elif all(k.startswith("detector.") for k in missing_keys + unexpected_keys):
    #     print("\nTodas as não correspondências estavam dentro do módulo 'detector.'. Isto é esperado se o detector estava congelado ou sua estrutura mudou (ex: devido à fusão de camadas).")
    #     print("Os pesos para as partes treináveis (ResNet, classificadores) devem ter sido carregados corretamente.")
    # else:
    #     print("\nAviso: Houve não correspondências além do módulo 'detector.'. Por favor, revise cuidadosamente se outras partes deveriam ter sido treinadas e carregadas.")

    # 4. Prossiga com a avaliação
    # Certifique-se de que test_dl está definido corretamente e não está vazio
    if test_dl and len(test_dl.dataset) > 0:
        print("\nProsseguindo com a avaliação...")
        results = evaluate_model_task2(
            model_task2_eval,
            test_dl,
            device,
            num_osats_categories=8,
            num_scores_per_category=5,
            osats_category_names=['OSATS_RESPECT', 'OSATS_MOTION', 'OSATS_INSTRUMENT',
                                  'OSATS_SUTURE', 'OSATS_FLOW', 'OSATS_KNOWLEDGE',
                                  'OSATS_PERFORMANCE', 'OSATS_FINAL_QUALITY']
        )
        print("\nTupla de Resultados da Avaliação:", results)
    else:
        print("\nPulando a avaliação porque test_dl não é válido ou está vazio.")
        if test_dl:
            print(f"Tamanho do dataset do Test Dataloader: {len(test_dl.dataset)}")
        else:
            print("Test Dataloader (test_dl) é None.")

except FileNotFoundError:
    print(f"Erro Crítico: Arquivo de modelo não encontrado em {model_path}. Não é possível carregar os pesos.")
except AttributeError as ae:
    print(f"Erro de Atributo: {ae}")
    print("Isso pode significar que 'model_task2_eval' não é um objeto de modelo PyTorch válido ou é 'None'.")
    print("Verifique a instanciação do seu modelo.")
except Exception as e:
    print(f"Ocorreu um erro durante o carregamento do state_dict ou avaliação: {e}")
    import traceback
    traceback.print_exc()

Initializing YOLO detector (yolo_preTrained.pt) on device: cuda


Using cache found in /mounts/tf2/.cache/torch/hub/ultralytics_yolov5_master
YOLOv5 🚀 2025-7-23 Python-3.10.16 torch-2.7.0+cu128 CUDA:0 (NVIDIA RTX A6000, 48548MiB)



Fusing layers... 


Model summary: 212 layers, 20881221 parameters, 0 gradients, 47.9 GFLOPs


Adding AutoShape... 


...

/mounts/tf2/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:879: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


/mounts/tf2/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:879: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


/mounts/tf2/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:879: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


/mounts/tf2/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:879: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):



--- Métricas de Avaliação no Conjunto de Teste (Task 2) ---
Loss Médio por Predição Individual (CrossEntropy): 0.6528
Mean Absolute Error (MAE Médio por Categoria, 0-indexed): 0.2673
F1 Score (Macro Overall - Média dos F1-macro por Categoria): 0.6085
F1 Score (Weighted Overall - Média Ponderada dos F1-weighted por Categoria): 0.7384
F1 Score (Samples - Média das F1 por Amostra): 0.7442
Acurácia (Média por Categoria OSATS): 0.7442
Acurácia (Exact Match Ratio / Correspondência Exata do Subconjunto): 0.1974

--- Relatório de Classificação Detalhado por Categoria OSATS ---

-- OSATS_RESPECT --
              precision    recall  f1-score   support

Score_0idx 0      0.960     0.857     0.906        56
Score_0idx 1      0.545     0.375     0.444        16
Score_0idx 2      0.541     0.556     0.548        36
Score_0idx 3      0.630     0.810     0.708        42
Score_0idx 4      0.000     0.000     0.000         2

    accuracy                          0.711       152
   macro avg      0.53